## CAB420 Final Assignment


# Importing Library and Read Data from CSV files


In [2]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import random

# Spliting data to trainning and testing set
from sklearn.model_selection import train_test_split
# Fitting Multiple Linear Regression to the trainning set
from sklearn.linear_model import LinearRegression, Lasso
from sklearn.cluster import KMeans
from sklearn.metrics import mean_squared_error, r2_score

# Matplotlib setting 
%config InlineBackend.print_figure_kwargs = {'bbox_inches':None}
%config InlineBackend.rc = {'font.size': 30, 'figure.figsize': (30.0, 20.0), 'figure.facecolor': (1, 1, 1, 0), 'figure.subplot.bottom': 0.125, 'figure.edgecolor': (1, 1, 1, 0), 'figure.dpi': 500}

## Data Preprocessing

In [45]:
def convert_dummy_movie_dataset():
    movies_dataset = pd.read_csv("./data/movies.csv")
                             
    # Set the index by movieId, This line of code only able to execute once
    movies_dataset.set_index('movieId', inplace = True)
                             
    # Convert genres to dummy variable dataset
    # movies_genres_dummy <- a dataframe contains the genres values for all the movies and using movieId as index
    movies_genres_dummy = movies_dataset['genres'].str.get_dummies(sep='|')
    # Remove (no genres listed) from dummy because all 0 can represent (no genres listed)
    movies_genres_dummy = movies_genres_dummy.drop(columns=["(no genres listed)"], axis=1)

    # Pre Processing for KMeans Algorithm finding the similar movies
    movies_dataset = movies_dataset.drop(columns=["genres"], axis=1)
    movies_dataset = pd.merge(movies_dataset, movies_genres_dummy, on = 'movieId', how = "left")
                             
    return movies_dataset.drop(columns=["title"], axis=1)

def generate_rating_dataset_With_avg_rating():
    # Import dataset
    rating_dataset = pd.read_csv("./data/ratings.csv")
    
    user_avg_rating = rating_dataset.groupby('userId')['rating'].mean().to_frame()
    user_avg_rating = user_avg_rating.rename(columns={"rating": "user_avg_rating"})

    movie_avg_rating = rating_dataset.groupby('movieId')['rating'].mean().to_frame()
    movie_avg_rating = movie_avg_rating.rename(columns={"rating": "movie_avg_rating"})

    rating_dataset = pd.merge(rating_dataset, user_avg_rating, on = 'userId', how = "left")
    rating_dataset = pd.merge(rating_dataset, movie_avg_rating, on = 'movieId', how = "left")

    return rating_dataset.drop(columns=["timestamp"], axis=1)

def get_movie_genres():
    return convert_dummy_movie_dataset().columns

def get_tags_dummy():
    tags_dataset = pd.read_csv("./data/tags.csv")
    tags_dataset['tag'] = tags_dataset['tag'].str.lower()
    # Currently we disable the userId
    return pd.get_dummies(tags_dataset).drop(columns=["timestamp", "userId"],axis=1)

tags_df = get_tags_dummy()

tags_df.loc[(tags_df['tag_family'] == 1)]

movieId  tag_"artsy"  tag_06 oscar nominated best movie - animation  \
49        410            0                                              0   
59       2124            0                                              0   
62       2953            0                                              0   
128     27808            0                                              0   
1856     3983            0                                              0   
1942     4801            0                                              0   
2163     6650            0                                              0   
2226     6993            0                                              0   

      tag_1900s  tag_1920s  tag_1950s  tag_1960s  tag_1970s  tag_1980s  \
49            0          0          0          0          0          0   
59            0          0          0          0          0          0   
62            0          0          0          0          0          0   
128           0          0          0          0          0          0   
1856          0          0          0          0          0          0   
1942          0          0          0          0          0          0   
2163          0          0          0          0          0          0   
2226          0          0          0          0          0          0   

      tag_1990s  ...  tag_world war i  tag_world war ii  tag_writing  \
49            0  ...                0                 0            0   
59            0  ...                0                 0            0   
62            0  ...                0                 0            0   
128           0  ...                0                 0            0   
1856          0  ...                0                 0            0   
1942          0  ...                0                 0            0   
2163          0  ...                0                 0            0   
2226          0  ...                0                 0            0   

      tag_wrongful imprisonment  tag_wry  tag_younger men  tag_zither  \
49                            0        0                0           0   
59                            0        0                0           0   
62                            0        0                0           0   
128                           0        0                0           0   
1856                          0        0                0           0   
1942                          0        0                0           0   
2163                          0        0                0           0   
2226                          0        0                0           0   

      tag_zoe kazan  tag_zombies  tag_zooey deschanel  
49                0            0                    0  
59                0            0                    0  
62                0            0                    0  
128               0            0                    0  
1856              0            0                    0  
1942              0            0                    0  
2163              0            0                    0  
2226              0            0                    0  

[8 rows x 1476 columns]

## Movie Dataset

In [4]:
movie_df = convert_dummy_movie_dataset();
movie_df.head()

Action  Adventure  Animation  Children  Comedy  Crime  Documentary  \
movieId                                                                       
1             0          1          1         1       1      0            0   
2             0          1          0         1       0      0            0   
3             0          0          0         0       1      0            0   
4             0          0          0         0       1      0            0   
5             0          0          0         0       1      0            0   

         Drama  Fantasy  Film-Noir  Horror  IMAX  Musical  Mystery  Romance  \
movieId                                                                       
1            0        1          0       0     0        0        0        0   
2            0        1          0       0     0        0        0        0   
3            0        0          0       0     0        0        0        1   
4            1        0          0       0     0        0        0        1   
5            0        0          0       0     0        0        0        0   

         Sci-Fi  Thriller  War  Western  
movieId                                  
1             0         0    0        0  
2             0         0    0        0  
3             0         0    0        0  
4             0         0    0        0  
5             0         0    0        0

## Rating Dataset

In [5]:
rating_df = generate_rating_dataset_With_avg_rating();
rating_df.head()

userId  movieId  rating  user_avg_rating  movie_avg_rating
0       1        1     4.0         4.366379          3.920930
1       1        3     4.0         4.366379          3.259615
2       1        6     4.0         4.366379          3.946078
3       1       47     5.0         4.366379          3.975369
4       1       50     5.0         4.366379          4.237745

## Merge two dataset, generate the full table

In [6]:
full_rating_dataset = pd.merge(rating_df, movie_df, on = 'movieId', how = "left")
full_rating_dataset.head()

userId  movieId  rating  user_avg_rating  movie_avg_rating  Action  \
0       1        1     4.0         4.366379          3.920930       0   
1       1        3     4.0         4.366379          3.259615       0   
2       1        6     4.0         4.366379          3.946078       1   
3       1       47     5.0         4.366379          3.975369       0   
4       1       50     5.0         4.366379          4.237745       0   

   Adventure  Animation  Children  Comedy  ...  Film-Noir  Horror  IMAX  \
0          1          1         1       1  ...          0       0     0   
1          0          0         0       1  ...          0       0     0   
2          0          0         0       0  ...          0       0     0   
3          0          0         0       0  ...          0       0     0   
4          0          0         0       0  ...          0       0     0   

   Musical  Mystery  Romance  Sci-Fi  Thriller  War  Western  
0        0        0        0       0         0    0        0  
1        0        0        1       0         0    0        0  
2        0        0        0       0         1    0        0  
3        0        1        0       0         1    0        0  
4        0        1        0       0         1    0        0  

[5 rows x 24 columns]

## Calculate all the average rating for the user by Genre

In [7]:
def generate_full_dataset():
    full_rating_dataset = pd.merge(rating_df, movie_df, on = 'movieId', how = "left")
    
    for genre in get_movie_genres():
        user_avg_genre_rating = full_rating_dataset.loc[(full_rating_dataset[genre] == 1)].groupby('userId')['rating'].mean().to_frame()
        user_avg_genre_rating['rating'] = user_avg_genre_rating['rating'] * 2
        user_avg_genre_rating = user_avg_genre_rating.rename(columns={"rating": "user_avg_"+ genre +"_rating"})
        full_rating_dataset = pd.merge(full_rating_dataset, user_avg_genre_rating, on = 'userId', how = "left")
    
    return full_rating_dataset.fillna(0)

full_rating_dataset = generate_full_dataset()
# full_rating_dataset.to_csv("full_rating.csv")
full_rating_dataset.head()

userId  movieId  rating  user_avg_rating  movie_avg_rating  Action  \
0       1        1     4.0         4.366379          3.920930       0   
1       1        3     4.0         4.366379          3.259615       0   
2       1        6     4.0         4.366379          3.946078       1   
3       1       47     5.0         4.366379          3.975369       0   
4       1       50     5.0         4.366379          4.237745       0   

   Adventure  Animation  Children  Comedy  ...  user_avg_Film-Noir_rating  \
0          1          1         1       1  ...                       10.0   
1          0          0         0       1  ...                       10.0   
2          0          0         0       0  ...                       10.0   
3          0          0         0       0  ...                       10.0   
4          0          0         0       0  ...                       10.0   

   user_avg_Horror_rating  user_avg_IMAX_rating  user_avg_Musical_rating  \
0                6.941176                   0.0                 9.363636   
1                6.941176                   0.0                 9.363636   
2                6.941176                   0.0                 9.363636   
3                6.941176                   0.0                 9.363636   
4                6.941176                   0.0                 9.363636   

   user_avg_Mystery_rating  user_avg_Romance_rating  user_avg_Sci-Fi_rating  \
0                 8.333333                 8.615385                    8.45   
1                 8.333333                 8.615385                    8.45   
2                 8.333333                 8.615385                    8.45   
3                 8.333333                 8.615385                    8.45   
4                 8.333333                 8.615385                    8.45   

   user_avg_Thriller_rating  user_avg_War_rating  user_avg_Western_rating  
0                  8.290909                  9.0                 8.571429  
1                  8.290909                  9.0                 8.571429  
2                  8.290909                  9.0                 8.571429  
3                  8.290909                  9.0                 8.571429  
4                  8.290909                  9.0                 8.571429  

[5 rows x 43 columns]

In [8]:
full_rating_dataset['rating'] = full_rating_dataset['rating'] * 2
full_rating_dataset['rating'] = full_rating_dataset['rating'].astype(int)

full_rating_dataset.head()

userId  movieId  rating  user_avg_rating  movie_avg_rating  Action  \
0       1        1       8         4.366379          3.920930       0   
1       1        3       8         4.366379          3.259615       0   
2       1        6       8         4.366379          3.946078       1   
3       1       47      10         4.366379          3.975369       0   
4       1       50      10         4.366379          4.237745       0   

   Adventure  Animation  Children  Comedy  ...  user_avg_Film-Noir_rating  \
0          1          1         1       1  ...                       10.0   
1          0          0         0       1  ...                       10.0   
2          0          0         0       0  ...                       10.0   
3          0          0         0       0  ...                       10.0   
4          0          0         0       0  ...                       10.0   

   user_avg_Horror_rating  user_avg_IMAX_rating  user_avg_Musical_rating  \
0                6.941176                   0.0                 9.363636   
1                6.941176                   0.0                 9.363636   
2                6.941176                   0.0                 9.363636   
3                6.941176                   0.0                 9.363636   
4                6.941176                   0.0                 9.363636   

   user_avg_Mystery_rating  user_avg_Romance_rating  user_avg_Sci-Fi_rating  \
0                 8.333333                 8.615385                    8.45   
1                 8.333333                 8.615385                    8.45   
2                 8.333333                 8.615385                    8.45   
3                 8.333333                 8.615385                    8.45   
4                 8.333333                 8.615385                    8.45   

   user_avg_Thriller_rating  user_avg_War_rating  user_avg_Western_rating  
0                  8.290909                  9.0                 8.571429  
1                  8.290909                  9.0                 8.571429  
2                  8.290909                  9.0                 8.571429  
3                  8.290909                  9.0                 8.571429  
4                  8.290909                  9.0                 8.571429  

[5 rows x 43 columns]

In [9]:
full_rating_dataset.sort_values("movieId")

userId  movieId  rating  user_avg_rating  movie_avg_rating  Action  \
0           1        1       8         4.366379          3.920930       0   
81531     517        1       8         2.386250          3.920930       0   
30517     213        1       7         3.827381          3.920930       0   
81082     514        1       8         3.311083          3.920930       0   
30601     214        1       6         2.863636          3.920930       0   
30721     216        1       6         3.664634          3.920930       0   
30885     217        1       8         2.761827          3.920930       0   
31524     219        1       7         3.165720          3.920930       0   
80373     509        1       8         3.216274          3.920930       0   
32052     220        1      10         3.963768          3.920930       0   
80168     504        1       8         3.821839          3.920930       0   
56128     372        1       6         3.355932          3.920930       0   
79907     500        1       8         3.244186          3.920930       0   
32840     223        1       7         3.273333          3.920930       0   
29936     206        1      10         4.040000          3.920930       0   
33044     226        1       7         3.476331          3.920930       0   
99534     610        1      10         3.688556          3.920930       0   
33670     229        1      10         3.738462          3.920930       0   
79296     492        1       8         3.867769          3.920930       0   
79119     490        1       7         3.159292          3.920930       0   
33898     232        1       7         3.250580          3.920930       0   
78360     488        1       9         3.882883          3.920930       0   
34760     233        1       6         3.300000          3.920930       0   
77950     484        1       9         3.814545          3.920930       0   
34910     234        1      10         3.504950          3.920930       0   
35301     239        1       8         4.026882          3.920930       0   
35580     240        1      10         3.914062          3.920930       0   
77222     483        1       8         3.618819          3.920930       0   
36173     247        1      10         3.746667          3.920930       0   
62294     414        1       8         3.391957          3.920930       0   
...       ...      ...     ...              ...               ...     ...   
7420       50   188301       6         2.780645          3.666667       1   
49860     318   188675       7         3.755973          3.500000       0   
30516     212   188751       9         3.590726          4.500000       0   
81478     514   188797       8         3.311083          4.000000       0   
49861     318   188833       9         3.755973          4.500000       0   
52001     338   189043       5         2.935897          2.500000       0   
52002     338   189111       6         2.935897          3.000000       0   
36373     248   189333       7         3.745098          3.750000       1   
27249     184   189333       8         3.705224          3.750000       1   
49862     318   189381       5         3.755973          2.500000       1   
30179     210   189547       2         4.079710          1.000000       1   
71998     462   189713       5         3.406593          2.500000       0   
7421       50   190183       7         2.780645          3.500000       0   
52003     338   190207       3         2.935897          1.500000       0   
52004     338   190209       8         2.935897          4.000000       0   
52005     338   190213       2         2.935897          1.000000       0   
52006     338   190215       3         2.935897          1.500000       0   
52007     338   190219       2         2.935897          1.000000       0   
52008     338   190221       2         2.935897          1.000000       0   
27250     184   191005       9         3.705224          4.500000       1   
272

## Linear Regression for Predicting a user how many marks will he/she giving to a movie according to he/she previous rating to other movie and the others how they rate this movie


In [28]:
X_df = full_rating_dataset.drop(columns=['rating','movieId'], axis=1)
y_df = full_rating_dataset.loc[:,'rating']

X = X_df.values
y = y_df.values

X_train, X_test, y_train, y_test = train_test_split(X,y, test_size = 0.2)

X_df.head()

userId  user_avg_rating  movie_avg_rating  Action  Adventure  Animation  \
0       1         4.366379          3.920930       0          1          1   
1       1         4.366379          3.259615       0          0          0   
2       1         4.366379          3.946078       1          0          0   
3       1         4.366379          3.975369       0          0          0   
4       1         4.366379          4.237745       0          0          0   

   Children  Comedy  Crime  Documentary  ...  user_avg_Film-Noir_rating  \
0         1       1      0            0  ...                       10.0   
1         0       1      0            0  ...                       10.0   
2         0       0      1            0  ...                       10.0   
3         0       0      0            0  ...                       10.0   
4         0       0      1            0  ...                       10.0   

   user_avg_Horror_rating  user_avg_IMAX_rating  user_avg_Musical_rating  \
0                6.941176                   0.0                 9.363636   
1                6.941176                   0.0                 9.363636   
2                6.941176                   0.0                 9.363636   
3                6.941176                   0.0                 9.363636   
4                6.941176                   0.0                 9.363636   

   user_avg_Mystery_rating  user_avg_Romance_rating  user_avg_Sci-Fi_rating  \
0                 8.333333                 8.615385                    8.45   
1                 8.333333                 8.615385                    8.45   
2                 8.333333                 8.615385                    8.45   
3                 8.333333                 8.615385                    8.45   
4                 8.333333                 8.615385                    8.45   

   user_avg_Thriller_rating  user_avg_War_rating  user_avg_Western_rating  
0                  8.290909                  9.0                 8.571429  
1                  8.290909                  9.0                 8.571429  
2                  8.290909                  9.0                 8.571429  
3                  8.290909                  9.0                 8.571429  
4                  8.290909                  9.0                 8.571429  

[5 rows x 41 columns]

## DecisionTree

In [11]:
from sklearn.ensemble import RandomForestClassifier
rfc = RandomForestClassifier(n_estimators=100)
rfc.fit(X_train, y_train)

rfc.score(X_train,y_train)

0.984603560271731

In [12]:
rfc.score(X_test,y_test)

0.339646965489885

In [13]:
yhat = rfc.predict(X_test)

yhat

array([8, 7, 8, ..., 6, 8, 5])

In [14]:
y_test

array([ 6,  9,  8, ...,  6, 10,  7])

## Naive Bayes Gaussian Models

In [46]:
df = pd.merge(rating_df, movie_df, on = 'movieId', how = "left")

df = pd.merge(df, tags_df, on = 'movieId', how = "left").fillna(0)

NB_X = df.drop(columns=['user_avg_rating','movie_avg_rating','rating'], axis=1)
NB_y = df['rating'] * 2
NB_y = NB_y.astype(int)


NB_X.head()

userId  movieId  Action  Adventure  Animation  Children  Comedy  Crime  \
0       1        1       0          1          1         1       1      0   
1       1        1       0          1          1         1       1      0   
2       1        1       0          1          1         1       1      0   
3       1        3       0          0          0         0       1      0   
4       1        3       0          0          0         0       1      0   

   Documentary  Drama  ...  tag_world war i  tag_world war ii  tag_writing  \
0            0      0  ...              0.0               0.0          0.0   
1            0      0  ...              0.0               0.0          0.0   
2            0      0  ...              0.0               0.0          0.0   
3            0      0  ...              0.0               0.0          0.0   
4            0      0  ...              0.0               0.0          0.0   

   tag_wrongful imprisonment  tag_wry  tag_younger men  tag_zither  \
0                        0.0      0.0              0.0         0.0   
1                        0.0      0.0              0.0         0.0   
2                        0.0      0.0              0.0         0.0   
3                        0.0      0.0              0.0         0.0   
4                        0.0      0.0              0.0         0.0   

   tag_zoe kazan  tag_zombies  tag_zooey deschanel  
0            0.0          0.0                  0.0  
1            0.0          0.0                  0.0  
2            0.0          0.0                  0.0  
3            0.0          0.0                  0.0  
4            0.0          0.0                  0.0  

[5 rows x 1496 columns]

In [ ]:
from sklearn.naive_bayes import GaussianNB
X_train, X_test, y_train, y_test = train_test_split( NB_X.values, NB_y.values , test_size = 0.2)

clf = GaussianNB()

clf.fit(X_train, y_train)

clf.score(X_train, y_train)

In [44]:
clf.score(X_test, y_test)

0.28072017216943995

# K-Means Algorithm Clustering Similar Movies

In [10]:
# The dataset will use in this case
movies_dataset.iloc[:,1:-3].head()

Adventure  Animation  Children  Comedy  Crime  Documentary  Drama  \
movieId                                                                      
1                1          1         1       1      0            0      0   
2                1          0         1       0      0            0      0   
3                0          0         0       1      0            0      0   
4                0          0         0       1      0            0      1   
5                0          0         0       1      0            0      0   

         Fantasy  Film-Noir  Horror  IMAX  Musical  Mystery  Romance  Sci-Fi  \
movieId                                                                        
1              1          0       0     0        0        0        0       0   
2              1          0       0     0        0        0        0       0   
3              0          0       0     0        0        0        1       0   
4              0          0       0     0        0        0        1       0   
5              0          0       0     0        0        0        0       0   

         Thriller  War  
movieId                 
1               0    0  
2               0    0  
3               0    0  
4               0    0  
5               0    0

In [11]:
# X only contains movie genres values
X = movies_dataset.iloc[:,1:-3].values

# Performs K = 1 to 50 for clustering the data
Ks = range(1,50)
# Array for saving inertias values for each K Clustering
inertias = []

# Loop K times 
for k in Ks:
    # Create KMeans
    model = KMeans(n_clusters = k)
    # Train KMeans 
    model.fit(X)
    inertias.append(model.inertia_)

# Plot inertias values vs K numbers 
plt.ylabel("inertias")
plt.xlabel("Numbers of K")
plt.plot(Ks,inertias,'-o')

## We Can see the result from the graph. The numbers of Inertias are dramatically decreased when k= 1 to k = 20, from 16000 to 6000. Then it becomes slow, from 6000 to 4000 when k = 21 to k=50. We should choose K = 20 in this case


In [12]:
# Create KMeans Algorithm to cluster the data in 20 groups 
model = KMeans(n_clusters = 20)

# Train KMeans
model.fit(X)

# Get the cluster values for each movie
labels = model.predict(X)

# Put the cluster value back to the dataset
movies_dataset['cluster'] = labels

# Save it into a new csv file, you can view the result in this csv file
movies_dataset.sort_values(by=['cluster']).to_csv("MovieCluster.csv")

## Hierarchy Clustering Similar Users


We need to create a new dataframe from the full rating dataset
The new dataframe should contains all the average rating the user previous rating for all the genre

In [13]:
# Previous full rating dataframe
full_rating_dataset['rating'] = full_rating_dataset['rating'].astype(float) / 2
full_rating_dataset

userId  movieId  rating  Action  Adventure  Animation  Children  \
0            1        1     4.0       0          1          1         1   
1            1        3     4.0       0          0          0         0   
2            1        6     4.0       1          0          0         0   
3            1       47     5.0       0          0          0         0   
4            1       50     5.0       0          0          0         0   
5            1       70     3.0       1          0          0         0   
6            1      101     5.0       0          1          0         0   
7            1      110     4.0       1          0          0         0   
8            1      151     5.0       1          0          0         0   
9            1      157     5.0       0          0          0         0   
10           1      163     5.0       1          0          0         0   
11           1      216     5.0       0          0          0         0   
12           1      223     3.0       0          0          0         0   
13           1      231     5.0       0          1          0         0   
14           1      235     4.0       0          0          0         0   
15           1      260     5.0       1          1          0         0   
16           1      296     3.0       0          0          0         0   
17           1      316     3.0       1          1          0         0   
18           1      333     5.0       0          0          0         0   
19           1      349     4.0       1          0          0         0   
20           1      356     4.0       0          0          0         0   
21           1      362     5.0       0          1          0         1   
22           1      367     4.0       1          0          0         0   
23           1      423     3.0       1          0          0         0   
24           1      441     4.0       0          0          0         0   
25           1      457     5.0       0          0          0         0   
26           1      480     4.0       1          1          0         0   
27           1      500     3.0       0          0          0         0   
28           1      527     5.0       0          0          0         0   
29           1      543     4.0       0          0          0         0   
...        ...      ...     ...     ...        ...        ...       ...   
100806     610   150401     3.0       1          0          0         0   
100807     610   152077     4.0       0          0          0         0   
100808     610   152081     4.0       1          1          1         1   
100809     610   152372     3.5       0          0          0         0   
100810     610   155064     3.5       0          0          0         0   
100811     610   156371     5.0       0          0          0         0   
100812     610   156726     4.5       0          0          0         0   
100813     610   157296     4.0       0          1          1         0   
100814     610   158238     5.0       0          0          0         0   
100815     610   158721     3.5       1          0          0         0   
100816     610   158872     3.5       0          0          1         0   
100817     610   158956     3.0       1          0          0         0   
100818     610   159093     3.0       1          0          0         0   
100819     610   160080     3.0       1          0          0         0   
100820     610   160341     2.5       1          0          0         0   
100821     610   160527     4.5       1          0          0         0   
100822     610   160571     3.0       0          0          0         0   
100823     610   160836     3.0       1          0          0         0   
100824     610   161582     4.0       0          0          0         0   
100825     610   161634     4.0       0          0          0         0   
100826     610   162350     3.5       1          0          0         0   
100827     610   163937     3.5  

In [14]:
def generate_avg_rating_df():
    #genres_list includes ['Action', 'Adventure', 'Animation', 'Children', etc...]
    genres_list = movies_genres_dummy.columns.values

    # Columns name variable for creating the new dataframe
    columns_name = ["userId"]
    # Create Columns name array
    for genres in genres_list:
        columns_name.append("AVG_" + genres + "_Rating")

    # initialize the dataframe     
    df = pd.DataFrame(columns=columns_name)

    for userId in range(1,full_rating_dataset['userId'].max() + 1):
        row_values = { 'userId': userId }
        for idx , genre in enumerate(genres_list):
            # Getting the user Dataframe for calculating the avg value for this genre
            user_df = full_rating_dataset.loc[(full_rating_dataset["userId"] == userId) & (full_rating_dataset[genre] == 1) ]
            # calculating the avg value for this genre
            avg = user_df["rating"].mean()

            row_values.update( { columns_name[idx + 1] : avg} )
            
        df = df.append( pd.Series(row_values), ignore_index = True )
    df[['userId']] = df[['userId']].astype(int)
    return df.fillna(0)


In [15]:
# generate avg rating dataframe
avg_df = generate_avg_rating_df()

avg_df.head()

userId  AVG_Action_Rating  AVG_Adventure_Rating  AVG_Animation_Rating  \
0       1           4.322222              4.388235              4.689655   
1       2           3.954545              4.166667              0.000000   
2       3           3.571429              2.727273              0.500000   
3       4           3.320000              3.655172              4.000000   
4       5           3.111111              3.250000              4.333333   

   AVG_Children_Rating  AVG_Comedy_Rating  AVG_Crime_Rating  \
0             4.547619           4.277108          4.355556   
1             0.000000           4.000000          3.800000   
2             0.500000           1.000000          0.500000   
3             3.800000           3.509615          3.814815   
4             4.111111           3.466667          3.833333   

   AVG_Documentary_Rating  AVG_Drama_Rating  AVG_Fantasy_Rating  \
0                0.000000          4.529412            4.297872   
1                4.333333          3.882353            0.000000   
2                0.000000          0.750000            3.375000   
3                4.000000          3.483333            3.684211   
4                0.000000          3.800000            4.142857   

   AVG_Film-Noir_Rating  AVG_Horror_Rating  AVG_IMAX_Rating  \
0                   5.0           3.470588         0.000000   
1                   0.0           3.000000         3.750000   
2                   0.0           4.687500         0.000000   
3                   4.0           4.250000         3.000000   
4                   0.0           3.000000         3.666667   

   AVG_Musical_Rating  AVG_Mystery_Rating  AVG_Romance_Rating  \
0            4.681818            4.166667            4.307692   
1            0.000000            4.000000            4.500000   
2            0.500000            5.000000            0.500000   
3            4.000000            3.478261            3.379310   
4            4.400000            4.000000            3.090909   

   AVG_Sci-Fi_Rating  AVG_Thriller_Rating  AVG_War_Rating  AVG_Western_Rating  
0           4.225000             4.145455        4.500000            4.285714  
1           3.875000             3.700000        4.500000            3.500000  
2           4.200000             4.142857        0.500000            0.000000  
3           2.833333             3.552632        3.571429            3.800000  
4           2.500000             3.555556        3.333333            3.000000

In [16]:
%matplotlib inline

from scipy.cluster.hierarchy import linkage, dendrogram
userRatings = avg_df.iloc[:,1:].values

mergings = linkage(userRatings, method='complete')

dendrogram(
    mergings,
    labels = range(0,611),
    leaf_rotation= 90,
)

plt.show()

In [17]:
# X only contains movie genres values
X2 = avg_df.iloc[:,1:].values

# Performs K = 1 to 50 for clustering the data
Ks2 = range(1,50)
# Array for saving inertias values for each K Clustering
inertias2 = []

# Loop K times 
for k in Ks2:
    # Create KMeans
    model = KMeans(n_clusters = k)
    # Train KMeans 
    model.fit(X2)
    inertias2.append(model.inertia_)

# Plot inertias values vs K numbers 
plt.ylabel("inertias")
plt.xlabel("Numbers of K")
plt.plot(Ks2,inertias2,'-o')

## From the Grpah above, We can see that the dramatic decrease stop around cluster = 14, So we use 14 to cluster the user group

In [18]:
from scipy.cluster.hierarchy import fcluster
labels = fcluster(mergings, 12, criterion = 'distance')

# Put the cluster value back to the dataset
avg_df['cluster'] = labels

# Save it into a new csv file, you can view the result in this csv file
avg_df.sort_values(by=['cluster']).to_csv("User_Cluster.csv")
labels

array([ 9,  3,  2,  6,  9,  9,  5,  9,  9, 10,  3, 10,  3,  9,  9,  7,  6,
        6,  5,  7,  9,  5,  7,  9, 10,  2,  9,  6,  6, 10,  7,  6,  9,  6,
        8,  5,  9,  7,  9,  8,  5,  6,  8, 11,  7,  8,  6, 11, 10,  5,  6,
        7,  4,  9,  2,  9,  6,  8,  7, 10,  3,  9,  6,  6,  3,  9,  8,  6,
        3,  7,  9,  3,  8,  4,  9,  6, 10, 10,  4, 10, 11,  7,  7,  6, 11,
        8, 11,  3,  7,  7,  6,  9,  8,  9,  7,  9, 10,  9,  9,  8, 11,  9,
        6,  9,  6, 10,  9,  8,  6,  7,  7,  8,  9, 11,  9,  9,  9,  3,  6,
       11,  7,  6,  9,  9,  6,  8,  5,  4,  9,  9,  7,  6,  9,  9,  6,  9,
        6, 10, 10,  6,  9,  8,  7,  7,  8,  2,  5, 10,  2, 11, 11,  7, 11,
       10,  5,  6,  2,  7, 10,  5, 11,  8, 11,  5,  9,  6,  9,  6,  7,  9,
        8,  8, 10,  9,  1,  9,  6,  7,  8,  9,  9,  6,  3,  7, 10,  6,  6,
        9, 10,  7,  7,  3, 10,  2,  9,  9,  3,  9,  6,  6,  8,  6,  9,  9,
        7,  8,  2,  2, 10, 10,  9,  9,  9, 11,  7,  6,  5,  5,  6,  7,  6,
        6,  6,  2, 11,  7